<h1>Table of Contents<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"><li><span><a href="#Checando-escolas-com-IDEB" data-toc-modified-id="Checando-escolas-com-IDEB-1"><span class="toc-item-num">1&nbsp;&nbsp;</span>Checando escolas com IDEB</a></span></li><li><span><a href="#IDEB" data-toc-modified-id="IDEB-2"><span class="toc-item-num">2&nbsp;&nbsp;</span>IDEB</a></span></li><li><span><a href="#Taxa-de-aprovação" data-toc-modified-id="Taxa-de-aprovação-3"><span class="toc-item-num">3&nbsp;&nbsp;</span>Taxa de aprovação</a></span></li></ul></div>

In [228]:
# %load first_cell.py
%reload_ext autoreload
%autoreload 2

from paths import RAW_PATH, TREAT_PATH, OUTPUT_PATH, FIGURES_PATH, MODEL_PATH

import os
from copy import deepcopy
import numpy as np
import pandas as pd
pd.options.display.max_columns = 999

import warnings
warnings.filterwarnings('ignore')

# Plotting
import plotly
import plotly.graph_objs as go
import cufflinks as cf
plotly.offline.init_notebook_mode(connected=True)

from utils import *

# Metrics
from plot_metrics import plot_roc, plot_confusion

cf.go_offline()
cf.set_config_file(offline=False, world_readable=True)

colorscale = ['#025951', '#8BD9CA', '#BF7F30', '#F2C124', '#8C470B', '#DFC27D']

In [229]:
df = pd.read_excel(RAW_PATH / 'saeb' / 'divulgacao_anos_finais-escolas-2017.xlsx', header=4)
df.head()

Sigla da UF  Código do Município      Nome do Município  Código da Escola  \
0         NaN                  NaN                    NaN               NaN   
1         NaN                  NaN                    NaN               NaN   
2         NaN                  NaN                    NaN               NaN   
3          RO            1100015.0  Alta Floresta D'Oeste        11024666.0   
4          RO            1100015.0  Alta Floresta D'Oeste        11024682.0   

                Nome da Escola       Rede Taxa de Aprovação - 2005 Unnamed: 7  \
0                          NaN        NaN                      NaN        NaN   
1                          NaN        NaN              6º a 9º ano         6º   
2                          NaN        NaN                      NaN        NaN   
3         EMEIEF BOA ESPERANCA  Municipal                        -          -   
4  EEEF EURIDICE LOPES PEDROSO   Estadual                       81       75.6   

  Unnamed: 8 Unnamed: 9 Unnamed: 10                  Unnamed: 11  \
0        NaN        NaN         NaN                          NaN   
1         7º         8º          9º  Indicador de Rendimento (P)   
2        NaN        NaN         NaN                          NaN   
3          -          -           -                            -   
4       86.2       84.5        74.4                     0.798345   

  Taxa de Aprovação - 2007 Unnamed: 13 Unnamed: 14 Unnamed: 15 Unnamed: 16  \
0                      NaN         NaN         NaN         NaN         NaN   
1              6º a 9º ano          6º          7º          8º          9º   
2                      NaN         NaN         NaN         NaN         NaN   
3                        -           -           -           -           -   
4                     80.1          73        81.7          75        92.9   

                   Unnamed: 17 Taxa de Aprovação - 2009 Unnamed: 19  \
0                          NaN                      NaN         NaN   
1  Indicador de Rendimento (P)              6º a 9º ano          6º   
2                          NaN                      NaN         NaN   
3                            -                     91.7          95   
4                     0.799422                       73        58.3   

  Unnamed: 20 Unnamed: 21 Unnamed: 22                  Unnamed: 23  \
0         NaN         NaN         NaN                          NaN   
1          7º          8º          9º  Indicador de Rendimento (P)   
2         NaN         NaN         NaN                          NaN   
3        82.6        92.9          96                     0.912955   
4        76.3          81        93.5                     0.750473   

  Taxa de Aprovação - 2011 Unnamed: 25 Unnamed: 26 Unnamed: 27 Unnamed: 28  \
0                      NaN         NaN         NaN         NaN         NaN   
1              6º a 9º ano          6º          7º          8º          9º   
2                      NaN         NaN         NaN         NaN         NaN   
3                        -           -           -           -           -   
4                     69.4          64        70.3        70.5        76.5   

                   Unnamed: 29 Taxa de Aprovação - 2013 Unnamed: 31  \
0                          NaN                      NaN         NaN   
1  Indicador de Rendimento (P)              6º a 9º ano          6º   
2                          NaN                      NaN         NaN   
3                            -                     72.8        69.2   
4                     0.700451                     76.5        71.8   

  Unnamed: 32 Unnamed: 33 Unnamed: 34                  Unnamed: 35  \
0         NaN         NaN         NaN                          NaN   
1          7º          8º          9º  Indicador de Rendimento (P)   
2         NaN         NaN         NaN                          NaN   
3        36.4        78.9          88                     0.606416   
4          60        74.3        95.1                     0.733024  

In [230]:
cols = df.columns

new_cols_name = ['sigla_uf', 'cod_municipio', 'nome_municipio', 'cod_inep', 'nome_escola', 'rede']
anos = [2005 + 2*i for i in range(7)]

taxa = ['taxa_aprovacao_{}_{}'.format(ano, serie) for ano in anos for serie in ['todos']+list(range(6,10))+['indicador']]
saeb = ['saeb_{}_{}'.format(ano, mod) for ano in anos for mod in ['mat', 'pt', 'media_padrao']]
ideb = ['ideb_{}'.format(ano) for ano in anos]
projecoes = ['projecoes_{}'.format(ano) for ano in anos[1:]+['2019', '2021']]


new_cols_name  = new_cols_name + taxa + saeb + ideb + projecoes

ideb_dic_cols = dict(zip(new_cols_name, cols))
ideb_dic_cols

{'sigla_uf': 'Sigla da UF',
 'cod_municipio': 'Código do Município',
 'nome_municipio': 'Nome do Município',
 'cod_inep': 'Código da Escola',
 'nome_escola': 'Nome da Escola',
 'rede': 'Rede',
 'taxa_aprovacao_2005_todos': 'Taxa de Aprovação - 2005',
 'taxa_aprovacao_2005_6': 'Unnamed: 7',
 'taxa_aprovacao_2005_7': 'Unnamed: 8',
 'taxa_aprovacao_2005_8': 'Unnamed: 9',
 'taxa_aprovacao_2005_9': 'Unnamed: 10',
 'taxa_aprovacao_2005_indicador': 'Unnamed: 11',
 'taxa_aprovacao_2007_todos': 'Taxa de Aprovação - 2007',
 'taxa_aprovacao_2007_6': 'Unnamed: 13',
 'taxa_aprovacao_2007_7': 'Unnamed: 14',
 'taxa_aprovacao_2007_8': 'Unnamed: 15',
 'taxa_aprovacao_2007_9': 'Unnamed: 16',
 'taxa_aprovacao_2007_indicador': 'Unnamed: 17',
 'taxa_aprovacao_2009_todos': 'Taxa de Aprovação - 2009',
 'taxa_aprovacao_2009_6': 'Unnamed: 19',
 'taxa_aprovacao_2009_7': 'Unnamed: 20',
 'taxa_aprovacao_2009_8': 'Unnamed: 21',
 'taxa_aprovacao_2009_9': 'Unnamed: 22',
 'taxa_aprovacao_2009_indicador': 'Unnamed: 23

In [231]:
df = df.drop([0,1,2], axis='index')
df = df.drop([43610, 43611, 43612], axis=0) # notas

df.columns = [i.upper() for i in ideb_dic_cols.keys()]

In [232]:
df.tail()

SIGLA_UF  COD_MUNICIPIO NOME_MUNICIPIO    COD_INEP  \
43605       DF      5300108.0       Brasília  53068106.0   
43606       DF      5300108.0       Brasília  53068114.0   
43607       DF      5300108.0       Brasília  53068122.0   
43608       DF      5300108.0       Brasília  53068149.0   
43609       DF      5300108.0       Brasília  53068211.0   

                     NOME_ESCOLA      REDE TAXA_APROVACAO_2005_TODOS  \
43605  CEF 02 DO RIACHO FUNDO II  Estadual                         -   
43606        CEF 27 DE CEILANDIA  Estadual                         -   
43607        CEF 28 DE CEILANDIA  Estadual                         -   
43608        CEF 32 DE CEILANDIA  Estadual                         -   
43609         CEF MIGUEL ARCANJO  Estadual                         -   

      TAXA_APROVACAO_2005_6 TAXA_APROVACAO_2005_7 TAXA_APROVACAO_2005_8  \
43605                     -                     -                     -   
43606                     -                     -                     -   
43607                     -                     -                     -   
43608                     -                     -                     -   
43609                     -                     -                     -   

      TAXA_APROVACAO_2005_9 TAXA_APROVACAO_2005_INDICADOR  \
43605                     -                             -   
43606                     -                             -   
43607                     -                             -   
43608                     -                             -   
43609                     -                             -   

      TAXA_APROVACAO_2007_TODOS TAXA_APROVACAO_2007_6 TAXA_APROVACAO_2007_7  \
43605                         -                     -                     -   
43606                         -                     -                     -   
43607                         -                     -                     -   
43608                         -                     -                     -   
43609                         -                     -                     -   

      TAXA_APROVACAO_2007_8 TAXA_APROVACAO_2007_9  \
43605                     -                     -   
43606                     -                     -   
43607                     -                     -   
43608                     -                     -   
43609                     -                     -   

      TAXA_APROVACAO_2007_INDICADOR TAXA_APROVACAO_2009_TODOS  \
43605                             -                         -   
43606                             -                         -   
43607                             -                         -   
43608                             -                         -   
43609                             -                         -   

      TAXA_APROVACAO_2009_6 TAXA_APROVACAO_2009_7 TAXA_APROVACAO_2009_8  \
43605                     -                     -                     -   
43606                     -                     -                     -   
43607                     -                     -                     -   
43608                     -                     -                     -   
43609                     -                     -                     -   

      TAXA_APROVACAO_2009_9 TAXA_APROVACAO_2009_INDICADOR  \
43605                     -                             -   
43606                     -                             -   
43607                     -                             -   
43608                     -                             -   
43609                     -                             -   

      TAXA_APROVACAO_2011_TODOS TAXA_APROVACAO_2011_6 TAXA_APROVACAO_2011_7  \
43605                         -                     -                     -   
43606                      69.2                  63.1                  72.6   
43607                      64.1                  57.3                    62   
43608                         -                     -                     -

In [233]:
df_clean = pd.read_csv(TREAT_PATH / 'analysis' / 'df_clean.csv', index_col=0)
df_clean.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 146214 entries, 112132289130 to 112980381895
Data columns (total 41 columns):
L1_NU_IDADE_REFERENCIA              146214 non-null int64
L1_IN_SEXO                          146214 non-null int64
L1_TP_COR_RACA                      146214 non-null int64
L1_IN_TRANSPORTE_PUBLICO            146214 non-null int64
L1_ID_TURMA                         146214 non-null int64
L2_CO_ENTIDADE                      146214 non-null int64
L1_IN_EVASAO                        146214 non-null int64
L1_IN_DISTORCAO                     146214 non-null int64
L1_IN_MUNICIPIO_NASC_RIO            146214 non-null int64
L1_IN_MUNICIPIO_NASC_MET            146214 non-null int64
L1_IN_MUNICIPIO_NASC_OUT            146214 non-null int64
L2_IN_MUNICIPIO_RIO                 146214 non-null int64
L2_IN_MUNICIPIO_MET                 146214 non-null int64
L2_IN_MUNICIPIO_OUT                 146214 non-null int64
L1_IN_DIF_MUN_ESCOLA_NASC           146214 non-null int64
L2

### Checando escolas com IDEB

In [234]:
df['COD_INEP'] = df['COD_INEP'].astype(int)
df_rj = df[df['COD_INEP'].isin(df_clean['L2_CO_ENTIDADE']) == True]

len(df_rj)

734

In [235]:
df_rj[['IDEB_2015', 'TAXA_APROVACAO_2015_9']].replace('-', np.nan).info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 734 entries, 25378 to 27683
Data columns (total 2 columns):
IDEB_2015                632 non-null float64
TAXA_APROVACAO_2015_9    635 non-null float64
dtypes: float64(2)
memory usage: 17.2 KB


In [236]:
df_rj = df_rj[df_rj['IDEB_2015'] != '-']
df_rj.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 632 entries, 25378 to 27683
Data columns (total 84 columns):
SIGLA_UF                         632 non-null object
COD_MUNICIPIO                    632 non-null float64
NOME_MUNICIPIO                   632 non-null object
COD_INEP                         632 non-null int64
NOME_ESCOLA                      632 non-null object
REDE                             632 non-null object
TAXA_APROVACAO_2005_TODOS        632 non-null object
TAXA_APROVACAO_2005_6            632 non-null object
TAXA_APROVACAO_2005_7            632 non-null object
TAXA_APROVACAO_2005_8            632 non-null object
TAXA_APROVACAO_2005_9            632 non-null object
TAXA_APROVACAO_2005_INDICADOR    632 non-null object
TAXA_APROVACAO_2007_TODOS        632 non-null object
TAXA_APROVACAO_2007_6            632 non-null object
TAXA_APROVACAO_2007_7            632 non-null object
TAXA_APROVACAO_2007_8            632 non-null object
TAXA_APROVACAO_2007_9            632 non-

In [ ]:
df_rj['']

In [143]:
len(df_clean['L2_CO_ENTIDADE'].unique())

837

In [144]:
df_clean['L1_IN_EVASAO'].value_counts()

0    100059
1     46409
Name: L1_IN_EVASAO, dtype: int64

In [145]:
df_clean[df_clean['L2_CO_ENTIDADE'].isin(df_rj['COD_INEP'])]['L1_IN_EVASAO'].value_counts()

0    57789
1    24822
Name: L1_IN_EVASAO, dtype: int64

In [146]:
df_clean[df_clean['L2_CO_ENTIDADE'].isin(df_rj['COD_INEP'])]['L1_IN_EVASAO'].value_counts(normalize=True)

0    0.699532
1    0.300468
Name: L1_IN_EVASAO, dtype: float64

### IDEB

In [74]:
df_clean = df_clean.merge(df_rj[['COD_INEP', 'IDEB_2015']].rename({'COD_INEP': 'L2_CO_ENTIDADE'}, axis=1), 
                          on='L2_CO_ENTIDADE', how='left')

In [77]:
t = df_clean[['IDEB_2015', 'L1_IN_EVASAO']].pivot(columns='L1_IN_EVASAO', values='IDEB_2015').rename(dic_evasao, axis=1)

t[['Não evadido', 'Evadido']].iplot(kind='hist', colors=[colorscale[1], colorscale[0]], theme='white',
                                    title='Distribuição do IDEB por situação', 
                                    xTitle='IDEB', yTitle='Número de alunos')

In [82]:
t = df_clean[['L2_CO_ENTIDADE', 'IDEB_2015']].drop_duplicates()

t.set_index('L2_CO_ENTIDADE').iplot(kind='hist', colors=[colorscale[1], colorscale[0]], theme='white',
        title='Distribuição do IDEB por escola', 
        xTitle='IDEB', yTitle='Número de escolas')

In [97]:
t = df_clean[['L2_CO_ENTIDADE', 'IDEB_2015', 'L1_IN_EVASAO']].replace('-', np.nan).groupby(['L2_CO_ENTIDADE', 'IDEB_2015']).agg([sum, 'count'])
t = t['L1_IN_EVASAO']

t['perc'] = t['sum']/t['count']
t.sort_values('IDEB_2015')

sum  count      perc
L2_CO_ENTIDADE IDEB_2015                      
33044384       1.8         55    150  0.366667
33099243       2.2         26     51  0.509804
33056358       2.3         19     54  0.351852
33055629       2.3         33    107  0.308411
33048304       2.3         23     78  0.294872
33103925       2.4          9     24  0.375000
33089108       2.5        237    457  0.518600
33048339       2.5         52    112  0.464286
33091447       2.5         49    161  0.304348
33051330       2.6         41    177  0.231638
33091390       2.6         25     75  0.333333
33048509       2.6         45    115  0.391304
33058679       2.6         46    148  0.310811
33048495       2.6         15     68  0.220588
33091757       2.6         32     89  0.359551
33046603       2.7         38     85  0.447059
33027285       2.7         49    115  0.426087
33055742       2.7         31     76  0.407895
33057702       2.7         70    192  0.364583
33008418       2.7         55    181  0.303867
33058466       2.7         25     85  0.294118
33103968       2.7         39    153  0.254902
33090149       2.7         63    205  0.307317
33099901       2.7         26     57  0.456140
33015279       2.8         61    146  0.417808
33027323       2.8        276    629  0.438792
33036640       2.8        175    449  0.389755
33044961       2.8         38     95  0.400000
33046514       2.8         53    140  0.378571
33098816       2.8         53    173  0.306358
...                       ...    ...       ...
33000670       5.2          6     24  0.250000
33115001       5.3         11     69  0.159420
33044406       5.3          2     22  0.090909
33001286       5.3         49    229  0.213974
33037965       5.3         47    190  0.247368
33005990       5.3         36    125  0.288000
33032220       5.3         25    117  0.213675
33043760       5.4         53    195  0.271795
33021082       5.4         12     65  0.184615
33001022       5.4          5     59  0.084746
33006679       5.5         38    155  0.245161
33029717       5.5         53    156  0.339744
33002312       5.5          6     24  0.250000
33037515       5.5         45    127  0.354331
33004749       5.5         10     48  0.208333
33001456       5.5         28    103  0.271845
33001332       5.6         16     67  0.238806
33097216       5.6         21     64  0.328125
33099278       5.6         14     71  0.197183
33005478       5.7          1     31  0.032258
33000042       5.8         40    120  0.333333
33007403       6.0         36    179  0.201117
33036209       6.1          7     29  0.241379
33033994       6.2        105    349  0.300860
33001316       6.3         21     95  0.221053
33005362       6.4          1     22  0.045455
33001014       6.4         14     62  0.225806
33023298       6.4          5     28  0.178571
33153795       6.9          3     38  0.078947
33066523       7.2          8     88  0.090909

[632 rows x 3 columns]

In [118]:
t.reset_index().set_index('IDEB_2015')['perc'].iplot(kind='scatter', mode='markers', theme='white',
                                                    xTitle='IDEB', yTitle='% de evasão', color=colorscale[-1],
                                                    title='Percentual de evasão por IDEB da escola')

### Taxa de aprovação

In [119]:
df_clean = df_clean.merge(df_rj[['COD_INEP', 'TAXA_APROVACAO_2015_9']].rename({'COD_INEP': 'L2_CO_ENTIDADE'}, axis=1), 
                          on='L2_CO_ENTIDADE', how='left')

In [124]:
t = df_clean[['L2_CO_ENTIDADE', 'TAXA_APROVACAO_2015_9']].drop_duplicates()

t.set_index('L2_CO_ENTIDADE').iplot(kind='hist', colors=colorscale[1], theme='white',
        title='Distribuição da taxa de aprovação por escola', 
        xTitle='TAXA_APROVACAO_2015_9', yTitle='Número de escolas')

In [137]:
t = df_clean[['L2_CO_ENTIDADE', 
              'TAXA_APROVACAO_2015_9', 
              'L1_IN_EVASAO']].replace('-', np.nan).groupby(['L2_CO_ENTIDADE', 
                                                             'TAXA_APROVACAO_2015_9']).agg([sum, 'count'])
t = t['L1_IN_EVASAO']

t['perc'] = t['sum']/t['count']
t.sort_values('TAXA_APROVACAO_2015_9')

t.reset_index().set_index('TAXA_APROVACAO_2015_9')['perc'].iplot(kind='scatter', mode='markers', theme='white',
                                                         color=colorscale[-1],
                                                         xTitle='TAXA_APROVACAO_2015_9', yTitle='% de evasão', 
                                                         title='Percentual de evasão por aprovação na escola (2015)')

In [218]:
np.exp(-0.4) / (1 + np.exp(-0.4))

0.401312339887548

In [221]:
np.exp(-2.9)

0.05502322005640723

In [222]:
np.exp(-2.9) / (1 + np.exp(-2.9))

0.05215356307841774

In [223]:
0.8034 + 0.0812

0.8846

In [224]:
0.8034 / (0.8034 + 3.29)

0.19626716177260958

In [225]:
0.888 / (0.888 + 3.29)

0.2125418860698899

In [227]:
0.20 / (0.20 + 3.29)

0.05730659025787965